In [1]:
import ee

# Trigger the authentication flow.
ee.Authenticate()

# Initialize the library.
ee.Initialize()

Enter verification code:  4/1AVHEtk68qoXJ726LSOAgCO8XfHxc7EBYY381ePzzylGJvqLTC1L8R3VZXiE



Successfully saved authorization token.


# MODIS

Source: https://developers.google.com/earth-engine/datasets/catalog/MODIS_061_MOD11A1

Tutorial: https://developers.google.com/earth-engine/tutorials/community/intro-to-python-api

In [192]:
# Import the MODIS land surface temperature collection.
lst = ee.ImageCollection("MODIS/061/MOD11A1")

In [209]:
# Initial date of interest (inclusive).
i_date = '2017-01-01'

# Final date of interest (exclusive).
f_date = '2022-01-01'

# Selection of appropriate bands and dates for LST.
lst = lst.select('LST_Day_1km', 'QC_Day').filterDate(i_date, f_date)

In [210]:
lst

In [211]:
# Reduce the LST collection by mean.
lst_img = lst.mean()

# Adjust for scale factor.
lst_img = lst_img.select('LST_Day_1km').multiply(0.02)

# Convert Kelvin to Celsius.
lst_img = lst_img.select('LST_Day_1km').add(-273.15)

In [212]:
# Define the urban location of interest as a point near NYC
lon = -73.974691
lat = 40.741374
poi = ee.Geometry.Point(lon, lat)

# Define a region of interest with a buffer zone of 100 km around NYC.
roi = poi.buffer(1e5)

In [213]:
import folium

my_map = folium.Map(location=[lat, lon], zoom_start=10)

In [214]:
def add_ee_layer(self, ee_image_object, vis_params, name):
    """Adds a method for displaying Earth Engine image tiles to folium map."""
    map_id_dict = ee.Image(ee_image_object).getMapId(vis_params)
    folium.raster_layers.TileLayer(
        tiles=map_id_dict['tile_fetcher'].url_format,
        attr='Map Data &copy; <a href="https://earthengine.google.com/">Google Earth Engine</a>',
        name=name,
        overlay=True,
        control=True
    ).add_to(self)

In [207]:
lst_vis_params = {
    'min': 10, 'max': 30, 'dimensions': 512, 'region': roi,
    'palette': ['blue', 'yellow', 'orange', 'red']}

my_map.add_ee_layer(lst_img, lst_vis_params, 'Land Surface Temperature')

folium.LayerControl(collapsed = False).add_to(my_map);

In [208]:
my_map

In [217]:
# Save to GeoTIFF
task = ee.batch.Export.image.toDrive(image=lst_img,
                                     description='lst_nyc',
                                     scale=30,
                                     region=roi,
                                     fileNamePrefix='lst_nyc',
                                     crs='EPSG:4326',
                                     fileFormat='GeoTIFF')

In [224]:
task.start()

In [226]:
task.status()

{'state': 'RUNNING',
 'description': 'lst_nyc',
 'creation_timestamp_ms': 1680712758430,
 'update_timestamp_ms': 1680712839463,
 'start_timestamp_ms': 1680712837146,
 'task_type': 'EXPORT_IMAGE',
 'attempt': 1,
 'id': 'BVVBZEY2KTJCLEFHJCEWGMO6',
 'name': 'projects/earthengine-legacy/operations/BVVBZEY2KTJCLEFHJCEWGMO6'}